## Activity 2: Extract and Repurpose Data.

### References:
#### 1. Lab2.pdf
#### 2. Kaggle Sqlite European Soccer Database - https://www.kaggle.com/
#### 3. Titanic Survivors Vignette - http://rstudio-pubs-static.s3.amazonaws.com/25402_590f6acfb2544355883f8dcf1c441dc6.html
#### 4. XML - https://www.tutorialspoint.com/r/r_xml_files.htm
#### 5. SQLite  - https://cran.r-project.org/web/packages/RSQLite/RSQLite.pdf
#### 6. CSV files - https://cran.r-project.org/doc/manuals/R-data.pdf or http://rprogramming.net/read-csv-in-r/

## Players and Team 

#### Load necessary Libraries

In [29]:
#install.packages("XML", repos='http://cran.us./r-project.org')
library(XML) 
library(plyr)
library(RSQLite)
library(dplyr)
#install.packages("sqldf", dependencies=TRUE, repos='http://cran.rstudio.com/')
library(sqldf)

#### Connect database using dbConnect

In [30]:
myDB <- "database.sqlite"
conn <- dbConnect(drv = SQLite(), dbname= myDB)

#### Check list of tables and their columns

In [32]:
dbListTables(conn)                                   #Lists all Tables in the Database
dbListFields(conn,"Team")                           #Lists all Fields of the specified Table from the Database
#dbListFields(conn,"Match")
#dbListFields(conn,"Team_Attributes")

[1] "Country"           "League"            "Match"            
[4] "Player"            "Player_Attributes" "Team"             
[7] "Team_Attributes"   "sqlite_sequence"

[1] "id"               "team_api_id"      "team_fifa_api_id" "team_long_name"  
[5] "team_short_name"

#### Test a query

In [35]:
test1 <- dbGetQuery(conn,"SELECT player_api_id,player_name FROM Player limit 10")
list(test1)

[[1]]
   player_api_id        player_name
1         505942 Aaron Appindangoye
2         155782    Aaron Cresswell
3         162549        Aaron Doran
4          30572      Aaron Galindo
5          23780       Aaron Hughes
6          27316         Aaron Hunt
7         564793         Aaron Kuhl
8          30895       Aaron Lennon
9         528212       Aaron Lennox
10        101042      Aaron Meijers

### 1. Player.csv

#### 1.a. Retrieve Player ID,Name,Overall Rating,GK Attributes using Player and Player Attributes Table

In [36]:
task1 <- 'SELECT p.player_api_id,replace(player_name,","," ") as player_name,max(overall_rating) as overall_rating, (gk_diving+gk_handling+gk_kicking+gk_positioning+gk_reflexes) AS gk_attributes FROM Player p inner join Player_Attributes pa WHERE p.player_api_id = pa.player_api_id GROUP BY p.player_api_id,p.player_name order by max(overall_rating) DESC'
result1 <-  dbGetQuery(conn, task1)
list(result1)

[[1]]
      player_api_id                              player_name overall_rating
1             30981                             Lionel Messi             94
2             30717                         Gianluigi Buffon             93
3             30829                             Wayne Rooney             93
4             30893                        Cristiano Ronaldo             93
5             39854                           Xavi Hernandez             92
6             39989                           Gregory Coupet             92
7             30626                            Thierry Henry             91
8             30627                               John Terry             91
9             30657                            Iker Casillas             91
10            30723                         Alessandro Nesta             91
11            30743                               Ronaldinho             91
12            30955                           Andres Iniesta             91
13            34520                          Fabio Cannavaro             91
14            19533                                   Neymar             90
15            22543                           Radamel Falcao             90
16            27299                             Manuel Neuer             90
17            30631                            Frank Lampard             90
18            30714                          Francesco Totti             90
19            30728                          David Trezeguet             90
20            30834                             Arjen Robben             90
21            30924                            Franck Ribery             90
22            35724                       Zlatan Ibrahimovic             90
23            38843                               Ze Roberto             90
24            40636                              Luis Suarez             90
25            41044                                     Kaka             90
26            30613                            Cesc Fabregas             89
27            30618                           Steven Gerrard             89
28            30661                             Carles Puyol             89
29            30690                                  Adriano             89
30            30709                                Luca Toni             89
31            30843                         Robin van Persie             89
32            30859                                Petr Cech             89
33            30865                            Nemanja Vidic             89
34            30909                              David Villa             89
35            30931                                     Cris             89
36            30989                              Julio Cesar             89
37            33639                             Samuel Eto'o             89
38            39774                                    Lucio             89
39           107417                              Eden Hazard             89
40            27301                      Marcelo Jose Bordon             88
41            30617                          Jamie Carragher             88
42            30620                            Rio Ferdinand             88
43            30648                             Jens Lehmann             88
44            30675                           Michael Essien             88
45            30684                  Juninho Pernambucano 20             88
46            30696                                Luis Figo             88
47            30716                          Marco Materazzi             88
48            30720                                     Dida             88
49            30725                             Pavel Nedved             88
50            30731                             Andrea Pirlo             88
51            30822                            Didier Drogba             88
52            30853                       

#### 1.b. Retrieve Player ID,Count(Player ID),Count(Number of Leagues) using Player and Match Table

In [37]:
task2 <- 'SELECT p.player_api_id,count(match_api_id),count(distinct league_id) FROM Player p inner join Match m on p.player_api_id = m.home_player_1 or p.player_api_id = m.home_player_2 or p.player_api_id = m.home_player_3 or p.player_api_id = m.home_player_4 or p.player_api_id = m.home_player_5 or p.player_api_id = m.home_player_6 or p.player_api_id = m.home_player_7 or p.player_api_id = m.home_player_8 or p.player_api_id = m.home_player_9 or p.player_api_id = m.home_player_10 or p.player_api_id = m.home_player_11 or p.player_api_id = m.away_player_1 or p.player_api_id = m.away_player_2 or p.player_api_id = m.away_player_3 or p.player_api_id = m.away_player_4 or p.player_api_id = m.away_player_5 or p.player_api_id = m.away_player_6 or p.player_api_id = m.away_player_7 or p.player_api_id = m.away_player_8 or p.player_api_id = m.away_player_9 or p.player_api_id = m.away_player_10 or p.player_api_id = m.away_player_11 group by p.player_api_id order by count(distinct league_id) DESC'
result2 <-  dbGetQuery(conn, task2)
list(result2)

[[1]]
      player_api_id count(match_api_id) count(distinct league_id)
1             42119                 175                         6
2            116750                 151                         5
3            178538                 105                         5
4             22543                 147                         4
5             24123                 130                         4
6             25816                  68                         4
7             26434                  94                         4
8             26489                  89                         4
9             26675                 141                         4
10            30477                  63                         4
11            30692                  35                         4
12            30841                 147                         4
13            30890                  90                         4
14            30918                 123                         4
15            31294                  88                         4
16            31300                 151                         4
17            32937                 101                         4
18            33074                  38                         4
19            36784                 178                         4
20            38229                 167                         4
21            38369                  88                         4
22            38700                  51                         4
23            38795                 118                         4
24            40004                  63                         4
25            40165                 121                         4
26            41877                  54                         4
27            46509                 173                         4
28            47547                 137                         4
29            71353                 116                         4
30            93484                 182                         4
31            96643                  97                         4
32           109060                 101                         4
33           129918                  89                         4
34           156534                  59                         4
35           156556                  41                         4
36           163199                  55                         4
37           163205                  72                         4
38           170775                  71                         4
39           176300                 134                         4
40           183548                  25                         4
41           213502                  17                         4
42           242887                  61                         4
43            11736                 116                         3
44            12245                  12                         3
45            15403                 174                         3
46            18518                  22                         3
47            18904                 164                         3
48            20401                 126                         3
49            23148                  60                         3
50            23779                  23                         3
51            23988                 110                         3
52            24132                  78                         3
53            24385                 134                         3
54            24450                  40                         3
55            24499                  33                         3
56            25541                 104                         3
57            25772                 147                         3
58            25815                 227                         3
59            25922                  32                         3
60            25990               

#### Merge Above columns (DataFrames) together

In [38]:
result = merge(result1,result2, by = c("player_api_id","player_api_id"),all=TRUE)
list(result)

[[1]]
      player_api_id                              player_name overall_rating
1              2625                        Patryk Rachwal 18             63
2              2752                              Diego Mainz             72
3              2768                              Jose Dorado             75
4              2770                         Ignacio Gonzalez             74
5              2790                              Alberto Rey             73
6              2796                           Javier Jimenez             69
7              2802                          Pablo Hernandez             82
8              2805                              Ruben Perez             76
9              2857                               Ivan Perez             72
10             2862                          Vicente Sanchez             76
11             2907                          Gregory Lacombe             68
12             2973                             Ugur Inceman             72
13             2977                    David Rivas Rodriguez             82
14             2983                             Jorge Molina             75
15             2984                          Sergio Aragones             75
16             3140                           Alexandre Hauw             69
17             3204                           Marat Izmailov             81
18             3263                           Kelly Berville             67
19             3264                       Abdelmalek Cherrad             62
20             3316                            Oscar Sanchez             71
21             3329                          Vincent Euvrard             64
22             3377                          Luca Belingheri             72
23             3441                 Aleksander Radosavljevic             71
24             3512                            Peter Halmosi             75
25             3517                       Alexandr Kerzhakov             82
26             3520                          Andrey Arshavin             86
27             4747                               Lee Wilkie             73
28             4863                           Boban Grncarov             66
29             4902                                   Iriney             77
30             4939                               Tim Clancy             64
31             4999                         Sebastian Olszar             59
32             5016                           Ibrahim Sidibe             65
33             5044                         Jeroen Verhoeven             68
34             5047                            Wilko de Vogt             61
35             5063                             Sander Duits             68
36             5184                    Gudmundur Steinarsson             62
37             5192                             Manuel Silas             72
38             5202                               Remy Gomis             73
39             5217                          Laurent Batlles             77
40             5223                          Raffaele Rubino             63
41             5233                     Iban Javier Cuadrado             73
42             5243                            Julio Alvarez             76
43             5247                              Perez Richi             67
44             5272                           Gary Coulibaly             68
45             5362                         Ifet Taljevic 23             60
46             5440                          Marjan Petkovic             67
47             5468                     Freddy Mombongo-Dues             62
48             5610                             Yann Jouffre             75
49             5629                          Bertrand Robert             73
50             5631                            Jeremy Blayac             68
51             5662                          Dimitri Bulykin             73
52             5686                       

#### Write data into CSV file

In [39]:
write.csv(result,file="player.csv",row.names=FALSE)

#### Check if properly written in the CSV

In [40]:
read.csv.sql("player.csv", sql = 'select * from file',eol="\n")

Warning message:
"closing unused connection 5 (player.csv)"Warning message:
"closing unused connection 4 (player.csv)"

player_api_id player_name                overall_rating gk_attributes
1     2625          "Patryk Rachwal 18"        63             153          
2     2752          "Diego Mainz"              72              53          
3     2768          "Jose Dorado"              75              64          
4     2770          "Ignacio Gonzalez"         74              60          
5     2790          "Alberto Rey"              73             144          
6     2796          "Javier Jimenez"           69             340          
7     2802          "Pablo Hernandez"          82              54          
8     2805          "Ruben Perez"              76              56          
9     2857          "Ivan Perez"               72             143          
10    2862          "Vicente Sanchez"          76              44          
11    2907          "Gregory Lacombe"          68              42          
12    2973          "Ugur Inceman"             72             143          
13    2977          "David Rivas Rodriguez"    82             104          
14    2983          "Jorge Molina"             75              55          
15    2984          "Sergio Aragones"          75             364          
16    3140          "Alexandre Hauw"           69             136          
17    3204          "Marat Izmailov"           81              53          
18    3263          "Kelly Berville"           67             115          
19    3264          "Abdelmalek Cherrad"       62              49          
20    3316          "Oscar Sanchez"            71             107          
21    3329          "Vincent Euvrard"          64              54          
22    3377          "Luca Belingheri"          72              46          
23    3441          "Aleksander Radosavljevic" 71              62          
24    3512          "Peter Halmosi"            75             143          
25    3517          "Alexandr Kerzhakov"       82              63          
26    3520          "Andrey Arshavin"          86              55          
27    4747          "Lee Wilkie"               73             128          
28    4863          "Boban Grncarov"           66              54          
29    4902          "Iriney"                   77              40          
30    4939          "Tim Clancy"               64              59          
...   ...           ...                        ...            ...          
11031 701154        "Kylian Mbappe Lottin"     65             42           
11032 703659        "Colin Trachsel"           51             48           
11033 704523        "Christopher Nkunku"       62             43           
11034 705484        "Eray Cumart"              52             32           
11035 706985        "Jordan Lyden"             58             53           
11036 710807        "Jonatan Montiel"          67             47           
11037 715642        "Aissa Laidouni"           59             61           
11038 716998        "Sebastien Lamonge"        56             46           
11039 717248        "Felipe Augusto"           64             59           
11040 717270        "Antoine Rabillard"        61             56           
11041 717557        "Levi Garcia"              64             49           
11042 719413        "Dorian Caddy"             64             54           
11043 720738        "Charles Traore"           55             52           
11044 721133        "Rafa Soares"              70             60           
11045 722766        "Charly Musonda"           71             36           
11046 723037        "Wanderson Lima"           53             54           
11047 725718        "Dennis van der Heijden"   60             54           
11048 726956        "Cedric Itten"             54             41           
11049 728125        "Christopher McLaughlin"   50             49           
11050 728414        "Justin Hoogma"            59             54           
11051 728478        "Kamil Jozwiak"            56     

### 2. Team.csv

#### 2.a. Retrieve Sum of BuildUp, Chance Creation and Defense Attributes using Team and Team Attributes

In [41]:
task3 <- 'SELECT ta.team_api_id,t.team_long_name,(IFNULL(buildUpPlaySpeed,0)+IFNULL(buildUpPlayDribbling,0)+IFNULL(buildUpPlayPassing,0)) as build_sum,(IFNULL(chanceCreationPassing,0)+IFNULL(chanceCreationCrossing,0)+IFNULL(chanceCreationShooting,0)) as chance_sum,(IFNULL(defencePressure,0)+IFNULL(defenceAggression,0)+IFNULL(defenceTeamWidth,0)) as defense_sum FROM Team_Attributes ta inner join Team t on ta.team_api_id = t.team_api_id GROUP BY ta.team_api_id,t.team_long_name order by max(build_sum) DESC'
result3 <-  dbGetQuery(conn, task3)
list(result3)

[[1]]
    team_api_id               team_long_name build_sum chance_sum defense_sum
1          9804                       Torino       209        189         125
2          8600                      Udinese       205        199         143
3          8194           Fortuna Düsseldorf       198        141         145
4          8033   Podbeskidzie Bielsko-Biala       193        166         102
5          8245                Korona Kielce       192        153         135
6          8024                  Widzew Lódz       190        184         139
7          8244                  Widzew Lódz       190        184         139
8        208931                        Carpi       190        160         115
9          9830                    FC Nantes       189        153         132
10         7943                     Sassuolo       188        186         137
11         8543                        Lazio       188        220         190
12         8533                Chievo Verona       187        170         156
13         8655             Blackburn Rovers       185        159         157
14         8485                     Aberdeen       184        181         143
15         8654              West Ham United       184        171         105
16        10233                        Genoa       184        168         123
17         8028                Piast Gliwice       183        169         129
18         8302                   Sevilla FC       183        148         142
19         8483                    Blackpool       183        176         131
20         8537                      Livorno       183        138         118
21         9776       Eintracht Braunschweig       183        157         109
22         8636                        Inter       182        203         114
23        10212                  CS Marítimo       182        186         126
24         8226          TSG 1899 Hoffenheim       180        161         167
25         9875                       Napoli       180        215         159
26         9925                       Celtic       180        178         165
27         6269                       Novara       179        168         138
28         8262              SV Darmstadt 98       179        174         129
29         9768                  Sporting CP       178        147         174
30         9772                   SL Benfica       178        185         171
31         9800                   St. Mirren       178        179         140
32         9905              1. FSV Mainz 05       178        137         165
33         2182                  Lech Poznan       176        185         157
34         9764               Gil Vicente FC       176        147         132
35         8177            Hertha BSC Berlin       175        169         152
36         8460              SC Paderborn 07       175        160         108
37         8530                      Catania       175        141         147
38         9831                     OGC Nice       175        149         167
39         7794                    SC Bastia       174        156         147
40         7842                Estoril Praia       174        139         150
41         8658              Birmingham City       174        204         144
42         8697             SV Werder Bremen       174        192         183
43         9847          Paris Saint-Germain       174        191         166
44       158085                    FC Arouca       174        160         109
45         9773                     FC Porto       173        190         178
46         9826               Crystal Palace       173        186         111
47         8661                 RCD Mallorca       172        163         156
48         9927                   Motherwell       172        149         146
49        10192               BSC Young Boys       172        151         128
50         8581                   Levante UD       171        168         155
51         8650 

#### 2.b. Retrieve Total Number of Goals (Home + Away) scored by all the Teams using Team and Match

In [45]:
task4 <- dbGetQuery(conn,"SELECT home_team_api_id,away_team_api_id,home_team_goal,away_team_goal FROM Match")
inter1 <- ddply(task4, .(away_team_api_id), summarize, away_goal=sum(away_team_goal))
inter2 <- ddply(task4, .(home_team_api_id), summarize, home_goal=sum(home_team_goal))
colnames(inter1) <- c("team_api_id", "away_goal")
colnames(inter2) <- c("team_api_id","home_goal")
result4 = merge(inter1,inter2, by = c("team_api_id","team_api_id"),all=TRUE)
result4$total_goal <- result4$away_goal + result4$home_goal
arrange(result4,desc(total_goal))

team_api_id away_goal home_goal total_goal
1    8634       354       495       849       
2    8633       338       505       843       
3    9925       306       389       695       
4    9823       271       382       653       
5    8640       282       370       652       
6    8593       287       360       647       
7    9931       275       344       619       
8    8456       241       365       606       
9    8455       250       333       583       
10  10260       244       338       582       
11   9825       267       306       573       
12   9772       247       321       568       
13   9847       236       332       568       
14   9789       253       298       551       
15   9885       236       307       543       
16   9773       246       295       541       
17   8650       237       294       531       
18   8686       231       299       530       
19  10192       210       319       529       
20   9906       203       321       524       
21   9875       211       303       514       
22   8611       220       289       509       
23   9748       208       289       497       
24   8564       225       271       496       
25   8636       216       280       496       
26  10229       213       279       492       
27  10235       198       291       489       
28  10267       185       299       484       
29   8178       213       270       483       
30   8586       226       255       481       
... ...         ...       ...       ...       
270   9891      17        18        35        
271   6269      15        19        34        
272   8479      17        17        34        
273   9858      12        22        34        
274 188163      19        15        34        
275   8234      11        22        33        
276 177361      12        21        33        
277   8344      12        20        32        
278   4170      12        19        31        
279   8460      10        21        31        
280   8550       5        26        31        
281   8295      12        18        30        
282   8398      11        19        30        
283   8690       7        23        30        
284   9746      13        17        30        
285   6547      12        17        29        
286   9765      11        18        29        
287   9776      11        18        29        
288   9912      13        16        29        
289   6351      13        15        28        
290   8549      11        17        28        
291   4064      14        13        27        
292   6367       8        19        27        
293   9878      12        15        27        
294   8357      16        10        26        
295  10213      10        16        26        
296   7992      11        14        25        
297   6631       9        15        24        
298   7869      10        12        22        
299 108893       7        14        21

#### Merge 2.a. and 2.b. together 

In [46]:
result = merge(result3,result4, by = c("team_api_id","team_api_id"),all=TRUE)
head(arrange(result,desc(total_goal)))


team_api_id team_long_name   build_sum chance_sum defense_sum away_goal
1 8634        FC Barcelona     122       141        191         354      
2 8633        Real Madrid CF   153       165        175         338      
3 9925        Celtic           180       178        165         306      
4 9823        FC Bayern Munich 105       205        175         271      
5 8640        PSV              153       125        128         282      
6 8593        Ajax             117       143        176         287      
  home_goal total_goal
1 495       849       
2 505       843       
3 389       695       
4 382       653       
5 370       652       
6 360       647

#### Write final result into team.csv file

In [48]:
write.csv(result,file="team.csv",row.names=FALSE)

### END OF Lab2 - Activity 2.A